In [ ]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
import json

# Define the path to your JSON file
file_path = '/content/drive/MyDrive/MasterThesis/captions_data_combined_all.json'

# Open and load the JSON data
with open(file_path, 'r') as file:
    captions_data = json.load(file)


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def summarize_captions(gpt2_caption, blip_caption, gpt2_weight=1, blip_weight=1):
    # Apply weights by concatenating the captions with their respective weights
    combined_text = (gpt2_caption + ' ') * gpt2_weight + (blip_caption + ' ') * blip_weight
    input_length = len(combined_text.split())  # Calculate the input length

    # Adjust summarization parameters based on the combined text length
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text

# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Set the weights for GPT-2 and BLIP captions
    gpt2_weight = 2  # Example: GPT-2 captions are given twice the importance of BLIP
    blip_weight = 1

    # Only proceed if both captions are available
    if gpt2_caption and blip_caption:
        summarized_caption = summarize_captions(gpt2_caption, blip_caption, gpt2_weight, blip_weight)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", truncation=True, padding=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity between the summarized caption and original captions
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        # Print the information for verification
        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_2_blip_1.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.80k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

config.json:   0%|          | 0.00/4.19k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/605M [00:00<?, ?B/s]

Summarized Caption:  a hot dog on a bun with mustard and ketchup  a person in a black
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6519937515258789
Summarized Caption:  A hot dog and a drink on a picnic table  a hot dog  a plate of hot dogs and
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8148513436317444
Summarized Caption:  A hot dog and a drink on a picnic table  a hot dog  a plate of hot dogs and
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8148513436317444
Summarized Caption:  A hot dog and a drink on a picnic table  a hot dog  a plate of hot dogs and
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8148513436317444
Summarized Caption:  A hot dog and a drink on a picnic table  a hot dog  a plate of hot dogs and
Most Similar Original Caption: A picture of two hot dog

Your max_length is set to 20, but your input_length is only 19. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a dog laying on the floor next to a pot is a white dog laying next to the trash can .
Most Similar Original Caption: a white dog lays down near his food bowl and the trash can 
Cosine Similarity Score: 0.907532274723053
Summarized Caption:  A row of bikes parked on a sidewalk is seen in a row of bicycles . The
Most Similar Original Caption: A lot of bikes parked next to each other on a sidewalk.
Cosine Similarity Score: 0.915338397026062
Summarized Caption:  a dog sitting in the back seat of a car is a dog in a car . A dog
Most Similar Original Caption: A small adorable dog riding inside of a car.
Cosine Similarity Score: 0.90035480260849
Summarized Caption:  A dog sitting on a motorcycle in a parking lot in a lot is a dog sitting
Most Similar Original Caption: A dog sitting on the side car of a motorcycle in parking lot.
Cosine Similarity Score: 0.8985511660575867
Summarized Caption:  a man sitting on a bench with a dog sits on a park bench with his dog
Most Simil

In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def summarize_captions(gpt2_caption, blip_caption, gpt2_weight=1, blip_weight=1):
    # Apply weights by concatenating the captions with their respective weights
    combined_text = (gpt2_caption + ' ') * gpt2_weight + (blip_caption + ' ') * blip_weight
    input_length = len(combined_text.split())  # Calculate the input length

    # Adjust summarization parameters based on the combined text length
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text

# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Set the weights for GPT-2 and BLIP captions
    gpt2_weight = 1
    blip_weight = 2

    # Only proceed if both captions are available
    if gpt2_caption and blip_caption:
        summarized_caption = summarize_captions(gpt2_caption, blip_caption, gpt2_weight, blip_weight)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", truncation=True, padding=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity between the summarized caption and original captions
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        # Print the information for verification
        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_1_blip_2.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


Summarized Caption:  a hot dog on a bun with mustard and ketchup  a person in a black
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6519937515258789
Summarized Caption:  a hot dog and a drink on a picnic table  a table with a plate of hot dogs and a cup of soda
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8350111842155457
Summarized Caption:  a hot dog and a drink on a picnic table  a table with a plate of hot dogs and a cup of soda
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8350111842155457
Summarized Caption:  a hot dog and a drink on a picnic table  a table with a plate of hot dogs and a cup of soda
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8350111842155457
Summarized Caption:  a hot dog and a drink on a picnic table  a table with a plate of hot dogs and a cup

Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a black dog laying on the floor next to a toilet  a black bear laying on
Most Similar Original Caption: The dog is laying on the bathroom floor next to the toilet.
Cosine Similarity Score: 0.8028056025505066
Summarized Caption:  a man and a dog on a street  a train car on a  train car
Most Similar Original Caption: A woman holding a dog on the road next to a train
Cosine Similarity Score: 0.796083927154541
Summarized Caption:  A dog is looking out the window of a car  a dog is sitting in the passenger seat of a
Most Similar Original Caption: A dog looking out the window of a car.
Cosine Similarity Score: 0.8560819625854492
Summarized Caption:  a dog looking out a window at a dog looks through a window . A dog looking
Most Similar Original Caption: A dog looks out a window with his nose poking out a little.
Cosine Similarity Score: 0.9315967559814453
Summarized Caption:  a dog is looking at the camera while a person watches  a dog sitting on a bed
Most Similar Origi

Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  a dog laying on the floor next to a pot is a white dog with a white collar . The dog was
Most Similar Original Caption: a white dog lays down near his food bowl and the trash can 
Cosine Similarity Score: 0.8365392088890076
Summarized Caption:  bikes parked on a sidewalk  a row of bikes parked in a sidewalk . bikes parked
Most Similar Original Caption: A lot of bikes parked next to each other on a sidewalk.
Cosine Similarity Score: 0.9205290079116821
Summarized Caption:  a dog sitting in the back seat of a car is a dog in a car . A dog
Most Similar Original Caption: A small adorable dog riding inside of a car.
Cosine Similarity Score: 0.90035480260849
Summarized Caption:  a dog sitting on a motorcycle in a parking lot is a motorcycle sitting in a lot
Most Similar Original Caption: A dog sitting on the side car of a motorcycle in parking lot.
Cosine Similarity Score: 0.8945477604866028
Summarized Caption:  a man sitting on a bench with a dog sits on a park bench wit

...

Summarized Caption:  cows are walking down a road  a group of cows walk down a dirt road .
Most Similar Original Caption: many cows walking on a road with trees near by
Cosine Similarity Score: 0.8899117708206177


Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  A herd of sheep walking down a street  a white car a car . A herd
Most Similar Original Caption: Several cows are in the public street by a car.
Cosine Similarity Score: 0.8027638792991638
Summarized Caption:  A herd of sheep walking down a street  a white car a car . A herd
Most Similar Original Caption: Several cows are in the public street by a car.
Cosine Similarity Score: 0.8027638792991638
Summarized Caption:  A kitchen with a sink, refrigerator, and cabinets can be a kitchen without a sink
Most Similar Original Caption: The counter in this kitchen is very cluttered.
Cosine Similarity Score: 0.8444033265113831
Summarized Caption:  A kitchen with a refrigerator, stove, sink and a window can be a kitchen with
Most Similar Original Caption: A kitchen filled with lots of cabinet space and a refrigerator.
Cosine Similarity Score: 0.8853135108947754
Summarized Caption:  a kitchen with a white counter top and a white sink is a kitchen without a white
Most Similar Or

Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a man with a beer in his hand  a man sitting in front of a computer
Most Similar Original Caption: A PICTURE OF A MAN WITH BEER BEHIND HIM 
Cosine Similarity Score: 0.8074131608009338
Summarized Caption:  bikes parked next to each other   a group of bikes parked together . bikes parked
Most Similar Original Caption: Several bicycles sit parked nest to each other.
Cosine Similarity Score: 0.8702681660652161
Summarized Caption:  A room with a refrigerator and a shelf with various items is a refrigerator . A room
Most Similar Original Caption: A room that has an open refrigerator in it.
Cosine Similarity Score: 0.9139612317085266
Summarized Caption:  A kitchen with a stove, sink, and a refrigerator is a kitchen without a refrigerator
Most Similar Original Caption: A kitchen has a stove burner on the counter.
Cosine Similarity Score: 0.8255633115768433
Summarized Caption:  a man in a bathroom brushing his teeth takes a picture of himself in the bathroom . a
Most Simila

In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=3):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text

# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.53  # Example prior weight for GPT-2
    blip_weight = 0.47  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_2_blip_1_3.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)
Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A hot dog is a hot dog on a bun with mustard and ketchup . A
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6862645745277405


Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A hot dog and a drink on a picnic table is a perfect combination for a hot
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.7393310070037842


Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


...

Summarized Caption:  a man in a kitchen cutting up food a woman preparing a meal . a man cutting
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8143443465232849


Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A kitchen is a kitchen with a stove, sink, and refrigerator . A kitchen with
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8575078845024109


Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  a kitchen with a stove, a sink, and a refrigerator a man standing . a
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7835849523544312
Summarized Caption:  A bathroom with a sink, mirror, and shower can be a bathroom without a sink
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.9238462448120117
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=3):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.47  # Example prior weight for GPT-2
    blip_weight = 0.53  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_1_blip_2_3.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 12. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=6)
Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a person in a black hoodie a hot dog a hot hot dog . a person
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6196665167808533


Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a table with a plate of hot dogs and a cup of soda a hot dog a
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8821949362754822


Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


...

Summarized Caption:  A woman preparing food a man in a man's house . A man preparing food for
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8317450881004333


Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A kitchen with a sink and a stove is a kitchen without a sink or stove .
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8529060482978821


Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  a man standing in a kitchen with a dog a dog is a kitchen . a man
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7744706273078918
Summarized Caption:  A bathroom with a sink and mirror in it is a bathroom without a mirror . A
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8788999319076538
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=4):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.47  # Example prior weight for GPT-2
    blip_weight = 0.53  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_1_blip_2_4.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 13. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=6)
Your max_length is set to 20, but your input_length is only 19. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  a person in a black hoodie a hot dog on a hotdog on a person
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6218259334564209


Your max_length is set to 20, but your input_length is only 19. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  A table with a plate of hot dogs and a cup of soda a hot dog and
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.8367483019828796


Your max_length is set to 20, but your input_length is only 19. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


...

Summarized Caption:  a woman preparing food a man in a man's house . a man preparing food in
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8289650678634644


Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A kitchen with a sink and a stove is a kitchen without a sink or stove .
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8529060482978821


Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A man standing in a kitchen with a dog a dog is a man standing with a
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7623958587646484
Summarized Caption:  a bathroom with a sink and mirror in it is a bathroom without a mirror . a
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8788999319076538
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=4):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.53  # Example prior weight for GPT-2
    blip_weight = 0.47  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_2_blip_1_4.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)
Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A hot dog is a hot dog on a bun with mustard and ketchup . A
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6862645745277405


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A hot dog and a drink on a picnic table is a picnic with a hot dog
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.7787172198295593


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


...

Summarized Caption:  a man in a kitchen cutting up food a woman preparing food . a man cutting up
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8142754435539246


Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  A kitchen with a stove, sink, and refrigerator can be a kitchen without a stove
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.868548572063446


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A man standing in a kitchen with a stove, a sink, and a refrigerator a
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7795259356498718
Summarized Caption:  a bathroom with a sink, mirror, and shower is a bathroom without a shower .
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8905937075614929
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=5):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.47  # Example prior weight for GPT-2
    blip_weight = 0.53  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_1_blip_2_5.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.80k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

Summarized Caption:  a woman preparing food a man in a kitchen . a man preparing food . a woman
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.810849130153656


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  a kitchen with a sink and a stove is a kitchen without a stove . a kitchen
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8515117168426514


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  a man standing in a kitchen with a dog a kitchen without a stove . a man
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7922943234443665
Summarized Caption:  a bathroom with a sink and mirror in it is a bathroom without a mirror . a
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8788999319076538
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=5):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.53  # Example prior weight for GPT-2
    blip_weight = 0.47  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_2_blip_1_5.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 18. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)
Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A hot dog is a hot dog on a bun with mustard and ketchup . A
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.6862645745277405


Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A hot dog and a drink on a picnic table a hot dog is a picnic .
Most Similar Original Caption: Table near car with a bicycle along side and a plate with two hot dogs and a coke.
Cosine Similarity Score: 0.7403286099433899


Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


...

Summarized Caption:  a man in a kitchen cutting up food a woman preparing food . a man cutting up
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8142754435539246


Your max_length is set to 20, but your input_length is only 19. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=9)


Summarized Caption:  A kitchen with a stove, sink, and refrigerator is a kitchen without a sink .
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8479976654052734


Your max_length is set to 20, but your input_length is only 17. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A man standing in a kitchen with a stove, a sink, and a refrigerator is
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7964925169944763
Summarized Caption:  a bathroom with a sink, mirror, and shower is a bathroom without a sink .
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8942817449569702
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=2):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text


# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.47  # Example prior weight for GPT-2
    blip_weight = 0.53  # Example prior weight for BLIP

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_1_blip_2_2.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.80k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

Summarized Caption:  A woman preparing food a man prepares food for a man . A man preparing food for
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8441600203514099


Your max_length is set to 20, but your input_length is only 13. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=6)


Summarized Caption:  A kitchen with a sink and a stove is a kitchen without a sink or stove .
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8529060482978821


Your max_length is set to 20, but your input_length is only 13. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=6)


Summarized Caption:  a man standing in a kitchen with a dog a kitchen is a kitchen . a man
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7889136075973511
Summarized Caption:  A bathroom is a bathroom with a sink and mirror in it a bathroom . A bathroom
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.8860052227973938
JSON file has been updated and saved.


In [ ]:
import torch
import json
from transformers import CLIPProcessor, CLIPModel, pipeline
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize, word_tokenize

# Initialize the summarization pipeline and CLIP components
summarizer = pipeline("summarization", model="sshleifer/distilbart-cnn-12-6")
clip_processor = CLIPProcessor.from_pretrained("openai/clip-vit-base-patch32")
clip_model = CLIPModel.from_pretrained("openai/clip-vit-base-patch32")

def select_key_phrases(text, num_phrases=2):
    words = word_tokenize(text)
    # Placeholder for a more sophisticated key phrase selection logic
    return ' '.join(words[:num_phrases])

def create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight):
    # Determine primary and secondary based on weights
    if gpt2_weight >= blip_weight:
        primary_caption = gpt2_caption
        secondary_caption = blip_caption
    else:
        primary_caption = blip_caption
        secondary_caption = gpt2_caption

    # Extract sentences from the primary caption
    primary_sentences = sent_tokenize(primary_caption)
    # Extract key phrases from the secondary caption
    secondary_key_phrases = select_key_phrases(secondary_caption)

    # Combine sentences and key phrases for summarization input
    combined_text = ' '.join(primary_sentences) + ' ' + secondary_key_phrases
    return combined_text

def summarize_combined_text(combined_text):
    # Summarization parameters
    input_length = len(combined_text.split())
    max_length_ratio = 0.75
    min_viable_length = 20
    max_length = max(min_viable_length, int(input_length * max_length_ratio))
    min_length = max(10, max_length // 2)

    # Generate summary
    summarized_text = summarizer(combined_text, max_length=max_length, min_length=min_length, do_sample=False)[0]['summary_text']
    return summarized_text

# Process each item in the JSON
for key, item in captions_data.items():
    gpt2_caption = item['generated_captions'].get('gpt2', '')
    blip_caption = item['generated_captions'].get('blip', '')

    # Weights for GPT-2 and BLIP captions
    gpt2_weight = 0.53
    blip_weight = 0.47

    if gpt2_caption and blip_caption:
        combined_text = create_combined_text_for_summarization(gpt2_caption, blip_caption, gpt2_weight, blip_weight)
        summarized_caption = summarize_combined_text(combined_text)

        # Encode the summarized caption and original captions to get embeddings
        inputs = clip_processor(text=[summarized_caption] + item['original_coco_captions'], return_tensors="pt", padding=True, truncation=True)
        embeddings = clip_model.get_text_features(**inputs)

        # Calculate cosine similarity
        similarities = [torch.cosine_similarity(embeddings[0], emb, dim=0).cpu().item() for emb in embeddings[1:]]
        most_similar_index = similarities.index(max(similarities))
        most_similar_caption = item['original_coco_captions'][most_similar_index]
        cosine_similarity_score = max(similarities)

        # Update the JSON structure with new information
        captions_data[key]['summarized_caption'] = summarized_caption
        captions_data[key]['most_similar_caption'] = most_similar_caption
        captions_data[key]['cosine_similarity_score'] = cosine_similarity_score

        print(f"Summarized Caption: {summarized_caption}")
        print(f"Most Similar Original Caption: {most_similar_caption}")
        print(f"Cosine Similarity Score: {cosine_similarity_score}")
        print("=" * 50)

# Specify the output path for the updated JSON data
output_path = '/content/drive/MyDrive/MasterThesis/weighted_summarization_gpt2_2_blip_1_2.json'  # Update this path as needed

# Save the modified JSON data to a new file
with open(output_path, 'w') as file:
    json.dump(captions_data, file, indent=4)

print("JSON file has been updated and saved.")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Your max_length is set to 20, but your input_length is only 15. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)
Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  A hot dog is a hot dog on a bun with mustard and ketchup a person
Most Similar Original Caption: some food is sticking out of a toy car
Cosine Similarity Score: 0.683885395526886


Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  a hot dog and a drink on a picnic table a table is a good way to
Most Similar Original Caption: A picture of two hot dogs and a cup of soda
Cosine Similarity Score: 0.7786206007003784


Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


...

Summarized Caption:  a man in a kitchen cutting up food a woman cutting up a woman . a man
Most Similar Original Caption: He is working on the meal while the dog is patiently waiting. 
Cosine Similarity Score: 0.8028759956359863


Your max_length is set to 20, but your input_length is only 16. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


Summarized Caption:  A kitchen is a kitchen with a stove, sink, and refrigerator . A kitchen with
Most Similar Original Caption: A kitchen with a lot of items sitting out. 
Cosine Similarity Score: 0.8575078845024109


Your max_length is set to 20, but your input_length is only 14. Since this is a summarization task, where outputs shorter than the input are typically wanted, you might consider decreasing max_length manually, e.g. summarizer('...', max_length=7)


Summarized Caption:  a kitchen with a stove, a sink, and a refrigerator a man . a kitchen
Most Similar Original Caption: A man points at the wall in his kitchen.
Cosine Similarity Score: 0.7821455597877502
Summarized Caption:  A bathroom is a bathroom with a sink, mirror, and shower . A bathroom with
Most Similar Original Caption: A bathroom with a sink, vanity and shower stall.
Cosine Similarity Score: 0.905206024646759
JSON file has been updated and saved.
